# Instalando e Importando Bibliotecas


### Pandas e Numpy

In [ ]:
import pandas as pd
import numpy as np

### NLTK
* Apoio ao pré-processamento de textos (tokenização, stopwords, radicalização)

In [ ]:
import nltk
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('rslp')
from nltk.tokenize import word_tokenize
from nltk.stem.porter import *

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package rslp to /root/nltk_data...
[nltk_data]   Unzipping stemmers/rslp.zip.


### Sklearn
* Construção do Modelo Espaço-Vetorial
* Medidas de Similaridade

In [ ]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.neighbors import kneighbors_graph

### Networkx e Plotly
* Construção de Redes k-NN
* Visualização Interativa de Grafos

In [ ]:
import plotly.graph_objects as go
import networkx as nx
from networkx.algorithms import community

### Métodos de apoio

In [ ]:
def remove_stopwords(text,stop_words):

  # tudo para caixa baixa
  s = str(text).lower()

  tokens = word_tokenize(s)

  # remove stopwords, dígitos, caracteres especiais e pontuações
  v = [word for word in tokens if not word in stop_words and word.isalnum() and not word.isdigit()]

  return v

def stemming(tokens,stemmer):
  tokens_stems = [stemmer.stem(word) for word in tokens]
  return tokens_stems

def meu_tokenizador(doc, stop_words=nltk.corpus.stopwords.words('portuguese'), stemmer=PorterStemmer()):
  tokens = remove_stopwords(doc,stop_words)
  return stemming(tokens,stemmer)


def get_cluster_descriptors(VSM, df_documentos, cluster_id, max_terms=3):
  df_descritors = pd.DataFrame()
  df_descritors['word'] = VSM.get_feature_names_out()
  df_descritors['tfidf_sum'] = VSM.transform(df_documentos[df_documentos.cluster==cluster_id]['text']).toarray().sum(axis=0)
  df_descritors.sort_values(by='tfidf_sum',ascending=False,inplace=True)

  num_docs = len(df_documentos[df_documentos.cluster==cluster_id]['text'])
  descriptors =  df_descritors[df_descritors.tfidf_sum > 0].head(max_terms).word.to_list()

  return num_docs,descriptors

# Usando TFIDF na ponderação dos termos


### Sobre a base textual
* Amostra textual sobre projetos de pesquisa que receberam investimento da NSF (National Science Foundation)

https://archive.ics.uci.edu/ml/datasets/NSF+Research+Award+Abstracts+1990-2003

### Lendo a base textual

In [ ]:
df_documentos = pd.read_csv('teste.csv',sep='\t')

df_documentos.reset_index(inplace=True,drop=True)
df_documentos

event_id                 date  \
0     b4b29e9b5537c1896129029bd976438c  2017-01-05 15:27:28   
1     125bf6fbeef15b17a1d4837127129bbe  2017-01-08 16:04:51   
2     aff14d48f09878b31e0575971fc8fec2  2017-01-08 14:04:51   
3     ca7ca58720fc9a2338894095ba6409f0  2017-01-05 13:27:28   
4     2a6e78e1226fc9c5f1c9061febf175d1  2017-01-09 14:57:25   
...                                ...                  ...   
8641  061b9b603b8043696558f309ab184857  2017-12-14 15:59:34   
8642  b3a86762a53202cc32b8773051a63b48  2017-12-11 15:15:00   
8643  a2aa3d517698a0c4586705b95cda38c2  2017-12-13 19:03:18   
8644  b6f07b1d0d4aebf8f518a1060567ceca  2017-05-10 21:45:08   
8645  01b55b43061f326cfd332c087e98ef2d  2017-12-21 10:46:34   

                                                  title  \
0     Após 2ª morte por febre amarela em SP, vacinaç...   
1     Casos de febre amarela em macacos na região pr...   
2     G1 - Casos de febre amarela em macacos na regi...   
3     Após 2ª morte por febre amarela em SP, vacinaç...   
4     Mortes por febre amarela põem em alerta cidade...   
...                                                 ...   
8641  Febre amarela já matou dez pessoas e 501 macac...   
8642  Postos ainda têm vacinas contra Febre Amarela ...   
8643  Febre amarela: veja lista de postos de vacinaç...   
8644  Confirmado primeiro caso de febre amarela em p...   
8645  Começa vacinação contra a febre amarela no ext...   

                           local  \
0            Ribeirao Preto (SP)   
1            Ribeirao Preto (SP)   
2     Sao Jose do Rio Preto (SP)   
3     Sao Jose do Rio Preto (SP)   
4     Sao Jose do Rio Preto (SP)   
...                          ...   
8641              Mairipora (SP)   
8642            Hortolandia (SP)   
8643                   Embu (SP)   
8644           Paulo Afonso (BA)   
8645  Sao Joao da Boa Vista (SP)   

                                                    url    lat    lng  
0     http://g1.globo.com/sp/ribeirao-preto-franca/n... -21.17 -47.81  
1     http://g1.globo.com/sao-paulo/sao-jose-do-rio-... -21.17 -47.81  
2     http://g1.globo.com/sao-paulo/sao-jose-do-rio-... -20.82 -49.37  
3     http://g1.globo.com/sp/ribeirao-preto-franca/n... -20.82 -49.37  
4     http://istoe.com.br/mortes-por-febre-amarela-p... -20.82 -49.37  
...                                                 ...    ...    ...  
8641  http://www.atribuna.com.br/noticias/noticias-d... -23.31 -46.58  
8642  http://liberal.com.br/cidades/hortolandia/post... -22.85 -47.22  
8643  https://g1.globo.com/sp/sao-paulo/noticia/febr... -23.64 -46.85  
8644  https://g1.globo.com/bahia/noticia/confirmado-...  -9.40 -38.22  
8645  https://istoe.com.br/comeca-vacinacao-contra-a... -21.96 -46.79  

[8646 rows x 7 columns]

In [ ]:
df_documentos = df_documentos[['text']].drop_duplicates()

In [ ]:
df_documentos.reset_index(inplace=True,drop=True)

In [ ]:
df_documentos

text  cluster
0     Após 2ª morte por febre amarela em SP, vacinaç...       14
1     Casos de febre amarela em macacos na região pr...       14
2     G1 - Casos de febre amarela em macacos na regi...       14
3     Mortes por febre amarela põem em alerta cidade...       14
4     Surto de Febre Amarela atinge cidade de Carati...       14
...                                                 ...      ...
4332  Febre amarela já matou dez pessoas e 501 macac...       14
4333  São Paulo registra 501 mortes de macacos por f...       25
4334  Postos ainda têm vacinas contra Febre Amarela ...       14
4335  Confirmado primeiro caso de febre amarela em p...       14
4336  Começa vacinação contra a febre amarela no ext...       14

[4337 rows x 2 columns]

### Modelo Espaço Vetorial + TFIDF
* Ponderação TFIDF
* Corte por DF (Document Frequency)

In [ ]:
VSM = TfidfVectorizer(tokenizer=meu_tokenizador,min_df=3)
X = VSM.fit_transform(df_documentos['text'])

In [ ]:
X

<4337x1126 sparse matrix of type '<class 'numpy.float64'>'
	with 34143 stored elements in Compressed Sparse Row format>

In [ ]:
df_word_tfidfs = pd.DataFrame()
df_word_tfidfs['word'] = VSM.get_feature_names()
df_word_tfidfs['tfidf_sum'] = X.toarray().sum(axis=0)
df_word_tfidfs.sort_values(by='tfidf_sum',ascending=False,inplace=True)
df_word_tfidfs.head(50)

/usr/local/lib/python3.7/dist-packages/sklearn/utils/deprecation.py:87: FutureWarning:

Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.



word   tfidf_sum
402         febr  363.340524
56       amarela  363.283248
236       contra  253.820813
660         mort  210.165585
1068   vacinação  181.143339
1061      vacina  171.787104
180         caso  161.119772
591       macaco  151.292204
219     confirma  119.239622
931         saúd  115.028624
638         mina  112.805629
907          rio   94.749740
372       estado   94.276551
985     suspeita   86.091660
975           sp   85.805107
909           rj   84.758536
986     suspeito   76.906346
630           mg   70.440515
796        posto   70.335705
709       número   66.533887
359           es   65.750778
634          mil   65.572779
885     registra   63.046491
553       jornal   62.991784
201        cidad   61.962936
456      governo   59.383953
86           apó   58.350694
805   prefeitura   57.032557
661        morto   55.810643
969         sobe   55.801061
220   confirmada   54.987404
308          diz   54.939535
935   secretaria   53.815502
1097     vitória   53.433553
755        paulo   53.420527
774       pessoa   52.658504
320         dose   48.338542
144       brasil   45.689380
526    investiga   45.123908
221   confirmado   44.749118
890       região   43.103255
654      morador   41.821312
291          dia   40.129212
449        gerai   39.428473
742        parqu   39.266687
1065     vacinar   39.027726
821      procura   38.264519
971         sobr   37.001698
119        bahia   36.087448
642   ministério   35.756036

# Analisando N-gramas

#### Bigramas

In [ ]:
VSM = TfidfVectorizer(tokenizer=meu_tokenizador,min_df=3,ngram_range=(2,2))
X = VSM.fit_transform(df_documentos['text'])

df_bigrams_tfidfs = pd.DataFrame()
df_bigrams_tfidfs['word'] = VSM.get_feature_names()
df_bigrams_tfidfs['tfidf_sum'] = X.toarray().sum(axis=0)
df_bigrams_tfidfs.sort_values(by='tfidf_sum',ascending=False,inplace=True)
df_bigrams_tfidfs.head(50)

/usr/local/lib/python3.7/dist-packages/sklearn/utils/deprecation.py:87: FutureWarning:

Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.



word   tfidf_sum
743         febr amarela  432.505702
556          contra febr  297.128291
1714    vacinação contra  184.343727
1683       vacina contra  149.445383
1068           mort febr  108.842898
447            caso febr   96.732174
1072         mort macaco   86.129574
1618       suspeita febr   81.675251
453        caso suspeito   73.219006
954          macaco febr   71.432103
1621       suspeito febr   70.797386
1686         vacina febr   62.393980
514        confirma mort   57.634635
1616          surto febr   42.471139
1320      procura vacina   39.181923
651          dose vacina   38.014832
1025          mina gerai   37.845770
184       amarela macaco   36.315652
130       amarela estado   34.745535
703          estado mina   33.553435
1529     secretaria saúd   33.196581
1315       primeiro caso   30.941619
358             apó mort   30.919341
193           amarela mg   30.119210
1580           sobr febr   29.315275
960         macaco morto   28.711749
197         amarela mina   27.567990
1007            mil dose   27.376047
705           estado rio   26.822268
1313       primeira mort   26.432148
1571         sobe número   26.218222
1080       mort suspeita   26.109180
1154         número mort   25.933908
95    amarela confirmada   25.876270
175       amarela jornal   25.826003
1448          risco febr   25.711325
125           amarela es   25.700441
1009          mil pessoa   25.564221
1151         número caso   24.711587
262          amarela rio   24.117811
114          amarela diz   24.084561
1282     posto vacinação   24.007969
1037     ministério saúd   23.958451
1703      vacinar contra   23.560098
1118         nest sábado   21.796265
1280          posto saúd   21.196547
87         amarela cidad   20.971247
908         jornal globo   19.945789
1084          morto febr   19.743860
1497       saúd confirma   19.598382

#### Trigramas

In [ ]:
VSM = TfidfVectorizer(tokenizer=meu_tokenizador,min_df=3,ngram_range=(3,3))
X = VSM.fit_transform(df_documentos['text'])

df_trigrams_tfidfs = pd.DataFrame()
df_trigrams_tfidfs['word'] = VSM.get_feature_names()
df_trigrams_tfidfs['tfidf_sum'] = X.toarray().sum(axis=0)
df_trigrams_tfidfs.sort_values(by='tfidf_sum',ascending=False,inplace=True)
df_trigrams_tfidfs.head(50)

/usr/local/lib/python3.7/dist-packages/sklearn/utils/deprecation.py:87: FutureWarning:

Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.



word   tfidf_sum
432            contra febr amarela  372.610600
1554         vacinação contra febr  221.894233
1528            vacina contra febr  183.229195
1088             mort febr amarela  116.511036
347              caso febr amarela  111.527166
1484         suspeita febr amarela   99.120030
982            macaco febr amarela   78.959494
1487         suspeito febr amarela   78.359956
352             caso suspeito febr   75.633113
1532           vacina febr amarela   74.815514
1091              mort macaco febr   72.299590
1483            surto febr amarela   50.393830
711            febr amarela macaco   40.379359
657            febr amarela estado   38.945493
1459             sobr febr amarela   35.746259
492             dose vacina contra   34.186532
1257         procura vacina contra   33.176662
1354            risco febr amarela   32.354710
720                febr amarela mg   32.253483
724              febr amarela mina   29.591402
395             confirma mort febr   29.483028
652                febr amarela es   29.214804
622        febr amarela confirmada   29.097548
702            febr amarela jornal   28.942699
789               febr amarela rio   28.693597
1100            mort suspeita febr   28.187660
397           confirma mort macaco   26.825060
641               febr amarela diz   26.495902
1544           vacinar contra febr   26.334610
1030               mil dose vacina   26.195093
614             febr amarela cidad   26.177378
1251            primeiro caso febr   24.545679
1557        vacinação febr amarela   24.447786
1245            primeira mort febr   22.149231
287                apó mort macaco   21.749809
736              febr amarela nest   21.300602
1223        posto vacinação contra   20.997007
1393             saúd febr amarela   20.849853
1102            morto febr amarela   20.549579
623        febr amarela confirmado   19.456706
1591           vítima febr amarela   18.958774
786            febr amarela região   18.547696
690     febr amarela intensificada   18.366571
587           febr amarela aumenta   17.917119
611             febr amarela causa   17.659715
419        confirmado febr amarela   17.440514
916         imunização contra febr   17.254054
924   intensifica vacinação contra   17.098570
758              febr amarela pode   16.944698
577          febr amarela ampliada   16.547473

#### Unigramas + Bigramas + Trigramas

In [ ]:
VSM = TfidfVectorizer(tokenizer=meu_tokenizador,min_df=3,ngram_range=(1,3))
X = VSM.fit_transform(df_documentos['text'])

In [ ]:
X = X.toarray()
X

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

# Identificando Clusters

In [ ]:
X = np.array(X)
length = np.sqrt((X**2).sum(axis=1))[:,None]
X = X / length

In [ ]:
from sklearn.cluster import KMeans
import numpy as np

kmeans = KMeans(n_clusters=30).fit(X)
kmeans.labels_



KeyboardInterrupt: ignored

Exception ignored in: 'sklearn.cluster._k_means_common._relocate_empty_clusters_dense'
Traceback (most recent call last):
  File "<__array_function__ internals>", line 2, in where
KeyboardInterrupt


KeyboardInterrupt: ignored

In [ ]:
from sklearn.cluster import MiniBatchKMeans
import numpy as np

kmeans = MiniBatchKMeans(n_clusters=30,
                         random_state=0,
                         batch_size=6).fit(X)


In [ ]:
df_documentos['cluster']=kmeans.labels_


In [ ]:
df_documentos[df_documentos.cluster==3][['text']]

text
1386  Febre amarela já provocou a morte de 70 pessoa...
1389  Febre amarela já provocou a morte de 70 pessoa...
1407  Febre amarela já provocou a morte de 70 pessoa...
1911  Estado investiga se febre amarela provocou mor...

# Gerando nossa rede k-NN

In [ ]:
A = kneighbors_graph(X, n_neighbors=15, metric="cosine")

In [ ]:
G = nx.Graph(A)

In [ ]:
for index,row in df_documentos.iterrows():
  G.nodes[index]['cluster'] = kmeans.labels_[index]

### Identificando clusters

In [ ]:
L_clusters = []
for index,row in df_documentos.iterrows():
  L_clusters.append(G.nodes[index]['cluster'])
df_documentos['cluster'] = L_clusters
df_documentos

text  cluster
0     Após 2ª morte por febre amarela em SP, vacinaç...       14
1     Casos de febre amarela em macacos na região pr...       14
2     G1 - Casos de febre amarela em macacos na regi...       14
3     Mortes por febre amarela põem em alerta cidade...       14
4     Surto de Febre Amarela atinge cidade de Carati...       14
...                                                 ...      ...
4332  Febre amarela já matou dez pessoas e 501 macac...       14
4333  São Paulo registra 501 mortes de macacos por f...       25
4334  Postos ainda têm vacinas contra Febre Amarela ...       14
4335  Confirmado primeiro caso de febre amarela em p...       14
4336  Começa vacinação contra a febre amarela no ext...       14

[4337 rows x 2 columns]

### Selecionando os termos com maiores TFIDF de um cluster

In [ ]:
df_documentos[df_documentos.cluster==17]

text  cluster
432   Jacareí tem primeiro caso suspeito de febre am...       17
444   G1 - Jacareí tem primeiro caso suspeito de feb...       17
658   Baixada Santista tem primeiro caso suspeito de...       17
839   Mato Grosso do Sul tem primeiro caso suspeito ...       17
929   Piauí registra primeiro caso suspeito de febre...       17
939   Piauí registra primeiro caso suspeito de febre...       17
942   Primeiro caso suspeito de febre amarela em Mat...       17
3273  Maricá tem primeiro caso suspeito de febre ama...       17
3278  Maricá, RJ, tem primeiro caso suspeito de febr...       17
3293  Maricá, RJ, tem primeiro caso suspeito de febr...       17
3371  Maricá, RJ, tem primeiro caso suspeito de febr...       17
4199  Jundiaí tem o primeiro caso suspeito de febre ...       17

In [ ]:
get_cluster_descriptors(VSM, df_documentos, 17)

(12, ['primeiro caso suspeito', 'primeiro caso', 'primeiro'])

In [ ]:
qtd_topics = 30

L = []
for cluster in df_documentos.cluster.unique():
  num_docs, descriptors = get_cluster_descriptors(VSM, df_documentos, cluster)
  if cluster==4: continue
  L.append([cluster,num_docs,descriptors])

df_descriptors = pd.DataFrame(L)
df_descriptors.columns = ['cluster','num_docs','descriptors']
df_descriptors.sort_values(by='num_docs',ascending=False).head(qtd_topics)

cluster  num_docs                                        descriptors
0        14      3383                      [febr, febr amarela, amarela]
1        12       195   [suspeito, suspeito febr amarela, suspeito febr]
2        24       193   [suspeita febr amarela, suspeita febr, suspeita]
8        25       192  [macaco febr, macaco febr amarela, mort macaco...
4        26        78            [dose vacina, dose, dose vacina contra]
7        20        66                          [gerai, mina gerai, mina]
15       13        36  [confirmado febr, confirmado febr amarela, cas...
21       19        30   [descarta febr, descarta febr amarela, descarta]
19       11        23         [amarela paulo, febr amarela paulo, paulo]
24       16        18      [amarela humano, febr amarela humano, humano]
5         9        16  [macaco suspeita, macaco suspeita febr, suspei...
14       17        12  [primeiro caso suspeito, primeiro caso, primeiro]
3        29        11                                [on, line, on line]
20       18         9  [pessoa contra febr, pessoa contra, mil pessoa...
23       22         9  [amarela região campina, região campina, febr ...
13        7         8  [mg confirma, mg confirma mort, governo mg con...
18       27         7  [amarela aplicada, febr amarela aplicada, apli...
26        2         6             [milhõ dose vacina, milhõ dose, milhõ]
12        6         6                   [dúvida, dúvida sobr febr, tira]
17        1         6      [descarta caso febr, descarta caso, descarta]
16        5         5   [mosquito, mosquito febr amarela, mosquito febr]
9        21         4                      [lança, saúd lança, campanha]
22        3         4  [amarela provoc, amarela provoc mort, febr ama...
10        0         4                  [oito mort febr, oito mort, oito]
11        8         4             [sob suspeita, sob suspeita febr, sob]
25       10         3           [tomar vacina febr, tomar vacina, tomar]
28       23         3         [quas macaco, mort quas macaco, mort quas]
6        15         2                      [saúd orienta, orienta, saúd]
27       28         2  [doi macaco, febr amarela confirmada, amarela ...

#### Mantendo apenas os documentos dos clusters selecionados
* O objetivo aqui é ressaltar os tópicos/temas mais relevantes da base de dados, conforme a estrutura da rede K-NN

In [ ]:
selected_clusters = df_descriptors.sort_values(by='num_docs',ascending=False).head(qtd_topics).cluster.to_list()
G2 = G.copy()
for node in G.nodes():
  if G.nodes[node]['cluster'] not in selected_clusters:
    G2.remove_node(node)

In [ ]:
pos = nx.spring_layout(G2,seed=42) # obtém coordenadas dos vértices para visualização
for node in G2.nodes():
  G2.nodes[node]['pos'] = pos[node]

In [ ]:
for index,row in df_documentos.iterrows(): # adiciona um texto em cada vértice.
  if index in G2.nodes:
    cluster_descriptor = str(df_descriptors[df_descriptors.cluster==G2.nodes[index]['cluster']].descriptors.to_list()[0])
    G2.nodes[index]['text'] = cluster_descriptor+"<br>"+str(row['text'])

##### Código para visualização interativa do grafo.
Fonte: https://plotly.com/python/network-graphs/

In [ ]:
def show_graph(G):
  ### ARESTAS
  edge_x = []
  edge_y = []

  # adicionando as coordenadas
  for edge in G.edges():
      x0, y0 = G.nodes[edge[0]]['pos']
      x1, y1 = G.nodes[edge[1]]['pos']
      edge_x.append(x0)
      edge_x.append(x1)
      edge_x.append(None)
      edge_y.append(y0)
      edge_y.append(y1)
      edge_y.append(None)

  # definindo cor e estilo das arestas
  edge_trace = go.Scatter(
      x=edge_x, y=edge_y,
      line=dict(width=2, color='#888'),
      hoverinfo='none',
      mode='lines')

  ### VÉRTICES
  node_x = []
  node_y = []

  # adicionando as coordenadas
  for node in G.nodes():
      x, y = G.nodes[node]['pos']
      node_x.append(x)
      node_y.append(y)

  # definindo cor e estilo dos vértices
  node_trace = go.Scatter(
      x=node_x, y=node_y,
      mode='markers',
      hoverinfo='text',
      marker=dict(
          size=10,
          line_width=2))


  # adicionando texto nos vértices
  node_text = []
  for node in G.nodes():
      node_text.append(G.nodes[node]['text'])
  node_trace.text = node_text

  # adicionando cores nos vértices de acordo com o cluster
  node_labels = []
  for node in G.nodes():
    node_labels.append(G.nodes[node]['cluster'])

  node_trace.marker.color = node_labels

  # visualizando!
  fig = go.Figure(data=[edge_trace, node_trace],
              layout=go.Layout(
                  showlegend=False,
                  hovermode='closest',
                  margin=dict(b=20,l=5,r=5,t=40),
                  xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                  yaxis=dict(showgrid=False, zeroline=False, showticklabels=False))
                  )
  fig.show()

### Visualização

In [ ]:
show_graph(G2)